In [85]:
import os
import requests
import itertools
import pandas as pd
from bs4 import BeautifulSoup
from tqdm import trange
import datasets as dst # to create a huggingface dataset

from chainfury.utils import threaded_map, to_json, from_json, get_files_in_folder

In [2]:
def _get_page_html(script, chapter_n, sutra_n, get_trans: bool = True, v: bool = False):
    translations = {
        "htrskd": 1, # Hindi Translation By Swami Ramsukhdas
        "httyn": 1, # Hindi Translation By Swami Tejomayananda
        "htshg": 1, # Hindi Translation Of Sri Shankaracharya's Sanskrit Commentary By Sri Harikrishnadas Goenka
        "scsh": 1, # Sanskrit Commentary By Sri Shankaracharya
        "hcchi": 1, # Hindi Commentary By Swami Chinmayananda
        "hcrskd": 1, # Hindi Commentary By Swami Ramsukhdas
        "scang": 1, # Sanskrit Commentary By Sri Abhinavgupta
        "scram": 1, # Sanskrit Commentary By Sri Ramanujacharya
        "scanand": 1, # Sanskrit Commentary By Sri Anandgiri
        "scjaya": 1, # Sanskrit Commentary By Sri Jayatirtha
        "scmad": 1, # Sanskrit Commentary By Sri Madhvacharya
        "scval": 1, # Sanskrit Commentary By Sri Vallabhacharya
        "scms": 1, # Sanskrit Commentary By Sri Madhusudan Saraswati
        "scsri": 1, # Sanskrit Commentary By Sri Sridhara Swami
        "scvv": 1, # Sanskrit Commentary By Sri Vedantadeshikacharya Venkatanatha
        "scpur": 1, # Sanskrit Commentary By Sri Purushottamji
        "scneel": 1, # Sanskrit Commentary By Sri Neelkanth
        "scdhan": 1, # Sanskrit Commentary By Sri Dhanpati
        "ecsiva": 1, # English Commentary By Swami Sivananda
        "etsiva": 1, # English Translation By Swami Sivananda
        "etpurohit": 1, # English Translation By Purohit Swami
        "etgb": 1, # English Translation By Swami Gambirananda
        "setgb": 1, # English Translation Of Sri Shankaracharya By Swami Gambirananda
        "etssa": 1, # English Translation By Dr. S. Sankaranarayan
        "etassa": 1, # English Translation of Abhinavgupta's Sanskrit Commentary By Dr. S. Sankaranarayan
        "etradi": 1, # English Translation of Ramanujacharya's Sanskrit Commentary By Swami Adidevananda
        "etadi": 1, # English Translation By Swami Adidevananda
    }
    params = {
        "language": script,
        "field_chapter_value": chapter_n,
        "field_nsutra_value": sutra_n,
        "show_mool": 1,
    }
    if get_trans:
        params.update(translations)
    r = requests.get(
        "https://www.gitasupersite.iitk.ac.in/srimad",
        params = params
    )
    if v:
        print(r.url)
    r.raise_for_status()
    soup = BeautifulSoup(r.text)

    # get the main shloka text first
    shloka_div = BeautifulSoup(
        str(soup.find_all("div", {"class": "views-field views-field-body"})[0].find_all("p")[0])
        .replace("<br/>", "\n")
    )
    shloka = shloka_div.getText().strip()

    # now find all the translations and store them
    data = {
        "id": f"{chapter_n}.{sutra_n}",
        "script": script,
        "body": shloka,
        "translations": []
    }
    for t in translations:
        trans_div = soup.find_all("div", {"class": f"views-field views-field-field-{t}"})
        if trans_div:
            all_p = trans_div[0].find_all("p")
            if all_p:
                trans_div = all_p[0]
                trans = trans_div.getText().strip()
                data["translations"].append({
                    "trans": t,
                    "content": trans
                })
    return data

def get_page_html(script, chapter_n, sutra_n, get_trans = True, pbar = None):
    try:
        out = _get_page_html(script, chapter_n, sutra_n, get_trans)
        pbar.update(1)
        return out, None
    except Exception as e:
        return (script, chapter_n, sutra_n), e

In [5]:
scripts = {
    "dv": "Devanagari",
    "as": "Assamese",
    "bn": "Bengali",
    "gu": "Gujarati",
    "pa": "Gurmukhi",
    "kn": "Kannada",
    "ml": "Malayalam",
    "or": "Odia",
    "ro": "Roman",
    "ta": "Tamil",
    "te": "Telugu",
}
chapter_to_max_sutra = {
  "1": 47,
  "2": 72,
  "3": 43,
  "4": 42,
  "5": 29,
  "6": 47,
  "7": 30,
  "8": 28,
  "9": 34,
  "10": 42,
  "11": 55,
  "12": 20,
  "13": 35,
  "14": 27,
  "15": 20,
  "16": 24,
  "17": 28,
  "18": 78,
}

items = []
for sc in list(scripts.keys())[:1]:
    for c in chapter_to_max_sutra:
        items.extend([(sc, int(c), i, True) for i in range(1,chapter_to_max_sutra[c]+1)])
len(items), items[:1]

(701, [('dv', 1, 1, True)])

In [8]:
data = _get_page_html(*items[0])
data = _get_page_html(*items[0][:3], False)
data

{'id': '1.1',
 'script': 'dv',
 'body': 'धृतराष्ट्र उवाच\n\n\n\nधर्मक्षेत्रे कुरुक्षेत्रे समवेता युयुत्सवः।\n\n\n\nमामकाः पाण्डवाश्चैव किमकुर्वत सञ्जय।।1.1।।',
 'translations': []}

## Create Gita singular dump

In [21]:
%%time

pbar = trange(len(items))
inputs = [(*x, pbar) for x in items]
translation_data = threaded_map(get_page_html, inputs, max_threads=10)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊| 700/701 [00:49<00:00, 14.38it/s]

CPU times: user 34.9 s, sys: 2.38 s, total: 37.3 s
Wall time: 49.8 s


In [22]:
failed_args = []
for (out, err) in translation_data:
    if err:
        failed_args.append(out)
len(translation_data), len(failed_args), len(inputs)

(701, 0, 701)

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 701/701 [01:02<00:00, 14.38it/s]

In [ ]:
translation_data[0]

In [11]:
# now download all the translations
script_items = []
for sc in list(scripts.keys()):
    for c in chapter_to_max_sutra:
        script_items.extend([(sc, int(c), i, False) for i in range(1,chapter_to_max_sutra[c]+1)])
len(script_items), script_items[:1]

(7711, [('dv', 1, 1, False)])

In [13]:
data = _get_page_html(*script_items[0])
data

{'id': '1.1',
 'script': 'dv',
 'body': 'धृतराष्ट्र उवाच\n\n\n\nधर्मक्षेत्रे कुरुक्षेत्रे समवेता युयुत्सवः।\n\n\n\nमामकाः पाण्डवाश्चैव किमकुर्वत सञ्जय।।1.1।।',
 'translations': []}

In [ ]:
%%time
pbar = trange(len(script_items))
inputs = [(*x, pbar) for x in script_items]
translit_data = threaded_map(get_page_html, inputs)

In [42]:
failed_args = []
for (out, err) in translit_data:
    if err:
        failed_args.append(out)
len(translit_data), len(failed_args), len(translit_data)

(7711, 0, 7711)

In [43]:
translit_data[0]

({'id': '1.1',
  'script': 'dv',
  'body': 'धृतराष्ट्र उवाच\n\n\n\nधर्मक्षेत्रे कुरुक्षेत्रे समवेता युयुत्सवः।\n\n\n\nमामकाः पाण्डवाश्चैव किमकुर्वत सञ्जय।।1.1।।',
  'translations': []},
 None)


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 7711/7711 [04:48<00:00,  8.77it/s]

In [69]:
# combine the translation and transliteration data
all_rows = []
for x, _ in translation_data:
    data = {
        "shloka_id": x["id"],
        "chapter": x["id"].split(".")[0],
        "sutra": x["id"].split(".")[1],
    }
    for t in x["translations"]:
        if ("did not comment on this sloka." in t["content"] or
            "No commentary" in t["content"]
        ):
            continue
        data["trans-" + t["trans"]] = t["content"]
    shloka_lits = list(filter(
        lambda y: y[0]["id"] == x["id"],
        translit_data
    ))
    for td, _ in shloka_lits:
        data[f"script-" + td["script"]] = td["body"]
    all_rows.append(data)

In [83]:
df_comb = pd.DataFrame(all_rows)
df_comb.head(4)

shloka_id chapter sutra                                       trans-htrskd  \
0       1.1       1     1  ।।1.1।। धृतराष्ट्र बोले (टिप्पणी प0 1.2) - हे ...   
1       1.2       1     2  ।।1.2।। संजय बोले - उस समय वज्रव्यूह-से खड़ी ह...   
2       1.3       1     3  ।।1.3।। हे आचार्य! आपके बुद्धिमान् शिष्य द्रुप...   
3       1.4       1     4  ।।1.4 -- 1.6।। यहाँ (पाण्डवों की सेना में) बड़...   

                                         trans-httyn  \
0  ।।1.1।।धृतराष्ट्र ने कहा -- हे संजय ! धर्मभूमि...   
1  ।।1.2।।संजय ने कहा -- पाण्डव-सैन्य की व्यूह रच...   
2  ।।1.3।।हे आचार्य ! आपके बुद्धिमान शिष्य द्रुपद...   
3  ।।1.4।।इस सेना में महान् धनुर्धारी शूर योद्धा ...   

                                         trans-hcchi  \
0  ।।1.1।। सम्पूर्ण गीता में यही एक मात्र श्लोक अ...   
1  ।।1.2।। इस श्लोक से आगे संजय ने कुरुक्षेत्र मे...   
2  ।।1.3।। वास्तव में दुर्योधन की यह मूर्खता है क...   
3                                                NaN   

                                        trans-hcrskd  \
0  1।।व्याख्या-- 'धर्मक्षेत्रे' 'कुरुक्षेत्रे'-- ...   
1  ।।1.2।। व्याख्या-- 'तदा'-- जिस समय दोनों सेनाए...   
2  1.3।। व्याख्या--'आचार्य' द्रोणके लिये 'आचार्य'...   
3  ।।1.4 --1.6।। व्याख्या--'अत्र शूरा महेष्वासा भ...   

                                         trans-scang  \
0  ।।1.1।।धर्मक्षेत्र इति।  अत्र केचित् व्याख्याव...   
1  ।।1.2  1.9।।किं वा अनेन बहुपरिगणनेन (K omits ब...   
2  ।।1.2  1.9।।किं वा अनेन बहुपरिगणनेन (K omits ब...   
3  ।।1.2  1.9।।किं वा अनेन बहुपरिगणनेन (K omits ब...   

                                         trans-scram  \
0  ।।1.1।।धृतराष्ट्र उवाच  सञ्जय उवाच  दुर्योधनः ...   
1  ।।1.2।।धृतराष्ट्र उवाच  सञ्जय उवाच  दुर्योधनः ...   
2  ।।1.3।।धृतराष्ट्र उवाच  सञ्जय उवाच  दुर्योधनः ...   
3  ।।1.4।।धृतराष्ट्र उवाच  सञ्जय उवाच  दुर्योधनः ...   

                                       trans-scanand  ...  \
0  ।।1.1।।एवं गीताशास्त्रस्य साध्यसाधनभूतनिष्ठाद्...  ...   
1  ।।1.2।।किमस्मदीयं प्रबलं बलं प्रतिलभ्य धीरपुरु...  ...   
2  ।।1.3।।तदेव वचनमुदाहरति   पश्येति।  एतामस्मदभ्...  ...   
3  ।।1.4।।अन्येऽपि प्रतिपक्षे पराक्रमभाजो बहवः सन...  ...   

                                           script-ml  \
0  ധൃതരാഷ്ട്ര ഉവാച\n\nധര്മക്ഷേത്രേ കുരുക്ഷേത്രേ സ...   
1  സഞ്ജയ ഉവാച\n\nദൃഷ്ട്വാ തു പാണ്ഡവാനീകം വ്യൂഢം ദ...   
2  പശ്യൈതാം പാണ്ഡുപുത്രാണാമാചാര്യ മഹതീം ചമൂമ്.\n\...   
3  അത്ര ശൂരാ മഹേഷ്വാസാ ഭീമാര്ജുനസമാ യുധി.\n\nയുയു...   

                                           script-or  \
0  ଧୃତରାଷ୍ଟ୍ର ଉବାଚ\n\nଧର୍ମକ୍ଷେତ୍ରେ କୁରୁକ୍ଷେତ୍ରେ ସ...   
1  ସଞ୍ଜଯ ଉବାଚ\n\nଦୃଷ୍ଟ୍ବା ତୁ ପାଣ୍ଡବାନୀକଂ ବ୍ଯୂଢଂ ଦ...   
2  ପଶ୍ଯୈତାଂ ପାଣ୍ଡୁପୁତ୍ରାଣାମାଚାର୍ଯ ମହତୀଂ ଚମୂମ୍|\n\...   
3  ଅତ୍ର ଶୂରା ମହେଷ୍ବାସା ଭୀମାର୍ଜୁନସମା ଯୁଧି|\n\nଯୁଯୁ...   

                                           script-ro  \
0  dhṛtarāṣṭra uvāca\n\ndharmakṣētrē kurukṣētrē s...   
1  sañjaya uvāca\n\ndṛṣṭvā tu pāṇḍavānīkaṅ vyūḍha...   
2  paśyaitāṅ pāṇḍuputrāṇāmācārya mahatīṅ camūm.\n...   
3  atra śūrā mahēṣvāsā bhīmārjunasamā yudhi.\n\ny...   

                                           script-ta  \
0  தரிதராஷ்ட்ர உவாச\n\nதர்மக்ஷேத்ரே குருக்ஷேத்ரே ...   
1  ஸஞ்ஜய உவாச\n\nதரிஷ்ட்வா து பாண்டவாநீகஂ வ்யூடஂ ...   
2  பஷ்யைதாஂ பாண்டுபுத்ராணாமாசார்ய மஹதீஂ சமூம்.\n\...   
3  அத்ர ஷூரா மஹேஷ்வாஸா பீமார்ஜுநஸமா யுதி.\n\nயுயு...   

                                           script-te trans-htshg trans-scsh  \
0  ధృతరాష్ట్ర ఉవాచ\n\nధర్మక్షేత్రే కురుక్షేత్రే స...         NaN        NaN   
1  సఞ్జయ ఉవాచ\n\nదృష్ట్వా తు పాణ్డవానీకం వ్యూఢం ద...         NaN        NaN   
2  పశ్యైతాం పాణ్డుపుత్రాణామాచార్య మహతీం చమూమ్.\n\...         NaN        NaN   
3  అత్ర శూరా మహేష్వాసా భీమార్జునసమా యుధి.\n\nయుయు...         NaN        NaN   

  trans-setgb trans-scjaya trans-scmad  
0         NaN          NaN         NaN  
1         NaN          NaN         NaN  
2         NaN          NaN         NaN  
3         NaN          NaN         NaN  

[4 rows x 41 columns]

In [71]:
not_na = df_comb.notna().sum().sum() / (df_comb.shape[0] * df_comb.shape[1])
na = (df_comb.notna()==False).sum().sum() / (df_comb.shape[0] * df_comb.shape[1])
print(f"fill: {not_na * 100:.2f}", )
print(f"empty: {na * 100:.2f}", )

fill: 96.72
empty: 3.28


In [78]:
gita_ds = dst.DatasetDict(train = dst.Dataset.from_pandas(df_comb))
gita_ds

DatasetDict({
    train: Dataset({
        features: ['shloka_id', 'chapter', 'sutra', 'trans-htrskd', 'trans-httyn', 'trans-hcchi', 'trans-hcrskd', 'trans-scang', 'trans-scram', 'trans-scanand', 'trans-scval', 'trans-scms', 'trans-scsri', 'trans-scvv', 'trans-scpur', 'trans-scneel', 'trans-scdhan', 'trans-ecsiva', 'trans-etsiva', 'trans-etpurohit', 'trans-etgb', 'trans-etssa', 'trans-etassa', 'trans-etradi', 'trans-etadi', 'script-dv', 'script-as', 'script-bn', 'script-gu', 'script-pa', 'script-kn', 'script-ml', 'script-or', 'script-ro', 'script-ta', 'script-te', 'trans-htshg', 'trans-scsh', 'trans-setgb', 'trans-scjaya', 'trans-scmad'],
        num_rows: 701
    })
})

In [82]:
%%time
gita_ds.push_to_hub("yashnbx/gita_supersite_dump")

Pushing split train to the Hub.


Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

CPU times: user 493 ms, sys: 99.8 ms, total: 593 ms
Wall time: 6 s


## Create the Sanskit TTS Dataset

In [20]:
# now download the audio clips
def get_audio(chapter_n: int, sutra_n: int, pbar = None):
    url = f"https://www.gitasupersite.iitk.ac.in/sites/default/files/audio/CHAP{chapter_n}/{chapter_n}-{sutra_n}.MP3"
    os.makedirs("./audio", exist_ok=True)
    r = requests.get(url, stream = True)
    fp = f'./audio/swami_brahmananda_{chapter_n}_{sutra_n}.mp3'
    with open(fp, 'wb') as mp3:
        for chunk in r.iter_content(chunk_size=int(1e5)):
            mp3.write(chunk)
    if pbar:
        pbar.update(1)
    return fp

In [ ]:
pbar = trange(len(items))
inputs = [(*x[1:], pbar) for x in items]
_ = threaded_map(get_audio, inputs)

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 701/701 [00:31<00:00, 44.19it/s]

In [89]:
for fp in get_files_in_folder("./audio"):
    print(fp)

In [110]:
audio_files = !ls ./audio/
audio_files = ["./audio/"+x for x in audio_files]
sample = []
for fp in audio_files:
    chapter_n, sutra_n = fp.split("_")[2:4]
    shloka_id = f"{chapter_n}.{sutra_n[:-4]}"
    _df = df_comb[df_comb.shloka_id == shloka_id]
    sample.append({
        "shloka_id": shloka_id,
        "text": _df["script-dv"].item(),
        "audio": fp
    })

In [116]:
tts_ds = dst.DatasetDict(
    train = dst.Dataset.from_list(sample).cast_column("audio", dst.Audio())
)

In [119]:
tts_ds["train"][0]

/opt/homebrew/lib/python3.10/site-packages/datasets/features/audio.py:310: UserWarning: Decoding mp3 with `librosa` instead of `torchaudio`, decoding is slow.
  warnings.warn("Decoding mp3 with `librosa` instead of `torchaudio`, decoding is slow.")


{'shloka_id': '10.1',
 'text': 'श्री भगवानुवाच\n\n\n\nभूय एव महाबाहो श्रृणु मे परमं वचः।\n\n\n\nयत्तेऽहं प्रीयमाणाय वक्ष्यामि हितकाम्यया।।10.1।।',
 'audio': {'path': './audio/swami_brahmananda_10_1.mp3',
  'array': array([ 0.0000000e+00,  0.0000000e+00,  0.0000000e+00, ...,
         -4.2175071e-07, -4.5091804e-07, -2.9115546e-07], dtype=float32),
  'sampling_rate': 16000}}

In [120]:
%%time
tts_ds.push_to_hub("yashnbx/gita_supersite_sanskrit_tts")

Pushing split train to the Hub.


  0%|          | 0/1 [00:00<?, ?ba/s]

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

CPU times: user 587 ms, sys: 148 ms, total: 734 ms
Wall time: 8.53 s
